In [4]:
%pip install pyvista
%pip install pyvirtualdisplay
%pip install skimage

# Import libraries
import numpy as np
import nibabel as nib
import pyvista as pv
from pyvirtualdisplay import Display

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
  Using cached skimage-0.0.tar.gz (757 bytes)
  Preparing metadata (setup.py) ... error
  error: subprocess-exited-with-error
  
  × python setup.py egg_info did not run successfully.
  │ exit code: 1
  ╰─> [3 lines of output]
      
      *** Please install the `scikit-image` package (instead of `skimage`) ***
      
      [end of output]
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.
Note: you may need to restart the kernel to use updated packages.


In [1]:
import time
import numpy as np
import nibabel as nib
import plotly.graph_objects as go

# Load NIfTI file
# Replace 'your_nifti_file.nii' with the path to your NIfTI file
vol = nib.load('someones_epi.nii.gz').get_fdata()
volume = vol.T  # Transpose if necessary based on your data orientation
r, c = volume[0].shape

# Define frames
nb_frames = volume.shape[0]

fig = go.Figure(frames=[
    go.Frame(
        data=go.Surface(
            z=k * np.ones((r, c)),
            surfacecolor=np.flipud(volume[k]),
            cmin=volume.min(),
            cmax=volume.max()
        ),
        name=str(k)
    )
    for k in range(nb_frames)
])

# Add initial data
fig.add_trace(go.Surface(
    z=0 * np.ones((r, c)),
    surfacecolor=np.flipud(volume[0]),
    colorscale='Gray',
    cmin=volume.min(),
    cmax=volume.max(),
    colorbar=dict(thickness=20, ticklen=4)
))

def frame_args(duration):
    return {
        "frame": {"duration": duration},
        "mode": "immediate",
        "fromcurrent": True,
        "transition": {"duration": duration, "easing": "linear"},
    }

sliders = [{
    "pad": {"b": 10, "t": 60},
    "len": 0.9,
    "x": 0.1,
    "y": 0,
    "steps": [
        {
            "args": [[f.name], frame_args(0)],
            "label": str(k),
            "method": "animate",
        }
        for k, f in enumerate(fig.frames)
    ],
}]

# Layout
fig.update_layout(
    title='Slices in Volumetric Data (NIfTI)',
    width=600,
    height=600,
    scene=dict(
        zaxis=dict(range=[-1, nb_frames], autorange=False),
        aspectratio=dict(x=1, y=1, z=1),
    ),
    updatemenus=[{
        "buttons": [
            {
                "args": [None, frame_args(50)],
                "label": "&#9654;",  # Play symbol
                "method": "animate",
            },
            {
                "args": [[None], frame_args(0)],
                "label": "&#9724;",  # Pause symbol
                "method": "animate",
            },
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 70},
        "type": "buttons",
        "x": 0.1,
        "y": 0,
    }],
    sliders=sliders
)

fig.show()
